In [1]:
from sentence_transformers import SentenceTransformer, util
import pandas as pd
import re

/Users/satoc/miniforge3/envs/gradio/lib/python3.12/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange


In [2]:
# Target列を分割する関数
def split_target(target):
    # 指定された区切り文字で分割
    split_words = re.split(r'[,\n、・及びおよび又はまたは]+', target)
    # 空白文字を除外してリストとして返す
    return [word.strip() for word in split_words if word.strip()]

In [3]:
basedf = pd.read_csv('../ClinicalTrialCSV/JRCT20241202Cancer.csv', index_col=0)
basedf = basedf.dropna(subset=['試験等のフェーズ'])
# Target列を分割してTargetWord列を追加
basedf['TargetWord'] = basedf['Target'].apply(split_target)

In [4]:
# モデルのロード
model = SentenceTransformer('all-MiniLM-L6-v2')

/Users/satoc/miniforge3/envs/gradio/lib/python3.12/site-packages/transformers/tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [9]:
# クエリ
#query = "乳がん"
query = "神経膠腫"
threshold = 0.7
# クエリをベクトル化
query_vec = model.encode(query, convert_to_tensor=True)


In [10]:
# ターゲットリスト全体を処理
matched_indices = []
target_vecs_list = []
cosine_scores_list = []
for idx, target_words in enumerate(basedf['TargetWord']):
    # ターゲット内の各単語をベクトル化
    target_vecs = model.encode(target_words, convert_to_tensor=True)
    # コサイン類似度を計算
    cosine_scores = util.cos_sim(query_vec, target_vecs).squeeze()
    target_vecs_list.append(target_vecs)
    cosine_scores_list.append(cosine_scores)
    # 閾値を超えるか確認
    if (cosine_scores >= threshold).any():  # いずれかが閾値を超えている場合
        matched_indices.append(idx)

# 抽出
matched_df = basedf.iloc[matched_indices]
matched_df

JRCT ID       NCT No JapicCTI No  \
72   jRCT2051240141  NCT05580562         NaN   
103  jRCT2051240121  NCT06413706         NaN   
224  jRCT2031240090          NaN         NaN   
286  jRCT2071230124  NCT06541665         NaN   
321  jRCT2071230114  NCT06240741         NaN   
370  jRCT2031230511          NaN         NaN   
387  jRCT2031230456          NaN         NaN   
459  jRCT2031230277          NaN         NaN   
473  jRCT2051230069          NaN         NaN   
529  jRCT2032230060          NaN         NaN   
549  jRCT2031230007          NaN         NaN   
563  jRCT2031220716          NaN         NaN   
633  jRCT2031220511  NCT05619744         NaN   
875  jRCT2031210299          NaN         NaN   

                                                 Title  \
72   新たに診断され放射線療法を完了したH3 K27M変異を有するびまん性神経膠腫の治療のためのO...   
103  放射線療法後の悪性神経膠腫の小児および若年成人を対象に、アベマシクリブ＋テモゾロミドとテモゾ...   
224  再発悪性神経膠腫に対する治療用放射性薬剤64Cu-ATSMの有効性を検証するランダム化比較医...   
286  ONO-4059-13:未治療の中枢神経系原発リンパ腫（PCNSL）を対象としたONO-40...   
321  日本の神経内分泌腫瘍（NEN）患者及び健康成人を対象に[68Ga]Ga-DOTA-TATEを...   
370  DAREON™-7：神経内分泌癌（NEC）患者の1次治療として，BI 764532点滴静注を...   
387  JCOG2107E: 切除不能・再発消化器（消化管・肝胆膵）神経内分泌癌（NEC）を対象とし...   
459  メトトレキサート基盤寛解導入療法後奏効例の非照射初発中枢神経系原発悪性リンパ腫に対するチラブ...   
473  神経膠腫患者に対するロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...   
529  初発IDH野生型低悪性度神経膠腫に対する交流電場腫瘍治療システムの有効性と安全性を検証する多...   
549  BRAF融合遺伝子陽性の進行・再発の低悪性度神経膠腫または膵癌に対するビニメチニブの第Ⅱ相医...   
563  DLL3を発現する小細胞肺癌及びその他の神経内分泌腫瘍の患者を対象としたBI 764532と...   
633  進行小細胞肺癌及びその他の神経内分泌癌患者を対象としてRO7616789の安全性，忍容性，薬...   
875                     再発悪性神経膠腫患者を対象としたDSP-0390の第1相試験   

                                                Target  \
72                            H3 K27M 変異を有する初発びまん性神経膠腫   
103                                             悪性神経膠腫   
224                                             悪性神経膠腫   
286                                        中枢神経系原発リンパ腫   
321                                       神経内分泌腫瘍（NEN）   
370  肺外神経内分泌癌（ただしメルケル細胞癌，甲状腺髄様癌又はグレード3の神経内分泌腫瘍を除く）\...   
387                                 消化器（消化管・肝胆膵）神経内分泌癌   
459                                      中枢神経系原発悪性リンパ腫   
473                                               神経膠腫   
529                        IDH野生型神経膠腫（グレードⅢ）（退形成性星細胞腫）   
549                                        低悪性度神経膠腫、膵癌   
563                        DLL3を発現する小細胞肺癌及びその他の神経内分泌腫瘍   
633                                  小細胞肺癌及びその他の神経内分泌癌   
875                                           再発悪性神経膠腫   

                                              研究・治験の目的 試験等のフェーズ 試験の種類  \
72   H3 K27M変異びまん性神経膠腫を有する被験者を対象に、放射線療法後に投与されたONC20...        3   NaN   
103  放射線療法後の悪性神経膠腫を有する小児および若年成人を対象に、アベマシクリブとテモゾロミドの...        2   NaN   
224  再発・難治性悪性神経膠腫を対象として、64Cu-diacetyl-bis（N4-methyl...        3   NaN   
286  未治療PCNSL患者を対象にONO-4059 とR-MPV 療法を併用投与したときの忍容性及...        1   NaN   
321  神経内分泌腫瘍（NEN）患者及び健康成人（HV）を対象に，[68Ga]Ga-DOTA-TAT...        3   NaN   
370  パートA：用量漸増の主要目的は，BI 764532の最大耐量（MTD）及び／又は目標用量の拡...        1   NaN   
387  切除不能・再発消化器（消化管・肝胆膵）神経内分泌癌（NEC）において、エトポシド＋カルボプラ...        3   NaN   
459  寛解導入療法として大量メトトレキサート（HD-MTX）基盤化学療法実施後に完全奏効（CRまた...        2   NaN   
473  神経膠腫患者におけるロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...        1   NaN   
529  初発IDH野生型低悪性度神経膠腫を対象に、放射線化学療法後のテモゾロミド維持療法期における交...        2   NaN   
549  BRAF融合遺伝子または遺伝子再構成陽性の切除不能または再発の低悪性度神経膠腫（コホート A...        2   NaN   
563  用量-毒性関係を評価し，ezabenlimab併用下でのBI 764532の最大耐量（MTD...        1   NaN   
633                                    非盲検多施設共同第Ⅰ相臨床試験        1   NaN   
875  再発悪性神経膠腫患者を対象にDSP-0390を経口投与したときの安全性、薬物動態、薬力学及び...        1   NaN   

        無作為化   盲検化  ...             purpose  \
72    無作為化比較  二重盲検  ...   treatment purpose   
103   無作為化比較   非盲検  ...   treatment purpose   
224   無作為化比較   非盲検  ...   treatment purpose   
286      単一群   非盲検  ...   treatment purpose   
321      単一群   非盲検  ...  diagnostic purpose   
370  非無作為化比較   非盲検  ...   treatment purpose   
387   無作為化比較   非盲検  ...   treatment purpose   
459   無作為化比較  二重盲検  ...   treatment purpose   
473      単一群   非盲検  ...   trea

In [11]:
# 全データのターゲット列をベクトル化
target_list = basedf['Target'].tolist()
target_vecs = model.encode(target_list, convert_to_tensor=True)
# コサイン類似度を計算
cosine_scores = util.cos_sim(query_vec, target_vecs).squeeze()

In [13]:
matched_indices_d = (cosine_scores >= threshold).nonzero().tolist()
# 入れ子リストをフラットなリストに変換
flat_indices_d = [idx[0] for idx in matched_indices_d]

# 抽出
matched_df_d = basedf.iloc[flat_indices_d]
matched_df_d


JRCT ID       NCT No JapicCTI No  \
103  jRCT2051240121  NCT06413706         NaN   
224  jRCT2031240090          NaN         NaN   
286  jRCT2071230124  NCT06541665         NaN   
321  jRCT2071230114  NCT06240741         NaN   
370  jRCT2031230511          NaN         NaN   
387  jRCT2031230456          NaN         NaN   
459  jRCT2031230277          NaN         NaN   
473  jRCT2051230069          NaN         NaN   
529  jRCT2032230060          NaN         NaN   
549  jRCT2031230007          NaN         NaN   
633  jRCT2031220511  NCT05619744         NaN   
875  jRCT2031210299          NaN         NaN   

                                                 Title  \
103  放射線療法後の悪性神経膠腫の小児および若年成人を対象に、アベマシクリブ＋テモゾロミドとテモゾ...   
224  再発悪性神経膠腫に対する治療用放射性薬剤64Cu-ATSMの有効性を検証するランダム化比較医...   
286  ONO-4059-13:未治療の中枢神経系原発リンパ腫（PCNSL）を対象としたONO-40...   
321  日本の神経内分泌腫瘍（NEN）患者及び健康成人を対象に[68Ga]Ga-DOTA-TATEを...   
370  DAREON™-7：神経内分泌癌（NEC）患者の1次治療として，BI 764532点滴静注を...   
387  JCOG2107E: 切除不能・再発消化器（消化管・肝胆膵）神経内分泌癌（NEC）を対象とし...   
459  メトトレキサート基盤寛解導入療法後奏効例の非照射初発中枢神経系原発悪性リンパ腫に対するチラブ...   
473  神経膠腫患者に対するロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...   
529  初発IDH野生型低悪性度神経膠腫に対する交流電場腫瘍治療システムの有効性と安全性を検証する多...   
549  BRAF融合遺伝子陽性の進行・再発の低悪性度神経膠腫または膵癌に対するビニメチニブの第Ⅱ相医...   
633  進行小細胞肺癌及びその他の神経内分泌癌患者を対象としてRO7616789の安全性，忍容性，薬...   
875                     再発悪性神経膠腫患者を対象としたDSP-0390の第1相試験   

                                                Target  \
103                                             悪性神経膠腫   
224                                             悪性神経膠腫   
286                                        中枢神経系原発リンパ腫   
321                                       神経内分泌腫瘍（NEN）   
370  肺外神経内分泌癌（ただしメルケル細胞癌，甲状腺髄様癌又はグレード3の神経内分泌腫瘍を除く）\...   
387                                 消化器（消化管・肝胆膵）神経内分泌癌   
459                                      中枢神経系原発悪性リンパ腫   
473                                               神経膠腫   
529                        IDH野生型神経膠腫（グレードⅢ）（退形成性星細胞腫）   
549                                        低悪性度神経膠腫、膵癌   
633                                  小細胞肺癌及びその他の神経内分泌癌   
875                                           再発悪性神経膠腫   

                                              研究・治験の目的 試験等のフェーズ 試験の種類  \
103  放射線療法後の悪性神経膠腫を有する小児および若年成人を対象に、アベマシクリブとテモゾロミドの...        2   NaN   
224  再発・難治性悪性神経膠腫を対象として、64Cu-diacetyl-bis（N4-methyl...        3   NaN   
286  未治療PCNSL患者を対象にONO-4059 とR-MPV 療法を併用投与したときの忍容性及...        1   NaN   
321  神経内分泌腫瘍（NEN）患者及び健康成人（HV）を対象に，[68Ga]Ga-DOTA-TAT...        3   NaN   
370  パートA：用量漸増の主要目的は，BI 764532の最大耐量（MTD）及び／又は目標用量の拡...        1   NaN   
387  切除不能・再発消化器（消化管・肝胆膵）神経内分泌癌（NEC）において、エトポシド＋カルボプラ...        3   NaN   
459  寛解導入療法として大量メトトレキサート（HD-MTX）基盤化学療法実施後に完全奏効（CRまた...        2   NaN   
473  神経膠腫患者におけるロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...        1   NaN   
529  初発IDH野生型低悪性度神経膠腫を対象に、放射線化学療法後のテモゾロミド維持療法期における交...        2   NaN   
549  BRAF融合遺伝子または遺伝子再構成陽性の切除不能または再発の低悪性度神経膠腫（コホート A...        2   NaN   
633                                    非盲検多施設共同第Ⅰ相臨床試験        1   NaN   
875  再発悪性神経膠腫患者を対象にDSP-0390を経口投与したときの安全性、薬物動態、薬力学及び...        1   NaN   

        無作為化   盲検化  ...             purpose  \
103   無作為化比較   非盲検  ...   treatment purpose   
224   無作為化比較   非盲検  ...   treatment purpose   
286      単一群   非盲検  ...   treatment purpose   
321      単一群   非盲検  ...  diagnostic purpose   
370  非無作為化比較   非盲検  ...   treatment purpose   
387   無作為化比較   非盲検  ...   treatment purpose   
459   無作為化比較  二重盲検  ...   treatment purpose   
473      単一群   非盲検  ...   treatment purpose   
529      単一群   非盲検  ...   treatment purpose   
549      単一群   非盲検  ...   treatment purpose   
633      単一群   非盲検  ...   treatment purpose   
875      単一群   非盲検  ...   treatment purpose   

                                    Inclusion Criteria  \
103  Subjects required to meet all the folloiwng cr...   
224  1) Histologically diagnosed as high grade glio...   
286  1. Patients diagnosed with PCNSL\r\n2. Patient...   
321  1. Signed informed consent must be obtained pr...   
370  - Male or female par